In [1]:
####################################################
# pyFIT3D SSP analysis simulation example
# --------------------------------------------------
# OBS: THIS EXAMPLE REQUIRED THE PACKAGE PANDAS
# --------------------------------------------------
# This example uses a SSP library and a file with
# the coeffs of each SSP model inside the library, 
# in order to to create a known age-metallicity 
# representative spectrum. 
# 
# Kinematics and dust extinction effects applyied.
#
# After this, the spectrum is analyzed using 
# pyFIT3D.common.auto_ssp_tools.auto_ssp_spec().
#
####################################################
# Althoug this example is not made this way, it 
# could be easily modifyed in order to create the 
# coeffs using tau-models (i.e., using timescales for 
# the formation of mass and for the age of the object), 
# allying also a max metallicity to the model.
####################################################
#
# Needed files:
#  - input real parameters file (real_parameters.csv)
#  - Foreach line in real pars file, a file with the 
# coeffs for the spectrum creation is needed.
#
# The input files with the coeffs requires to be
# formatted as:
#
#  - real_parameters.csv: Each line of the file 
# represents one input spectrum for the simulation. 
# The line should be composed of the non-linear 
# parameters (redshift, velocity dispersion and A_V, 
# the dust extinction parameter).
#
#    Example of parameters file:
# 
#    redshift,Av,LOSVD
#    0.03186,0.23318,314.72231
#    0.02176,0.42848,193.17778
#
#    Coeffs filenames for the parmeters file above:
#
#    coeffs_input.losvd314p7223-av0p2332-redshift0p0319.txt
#    coeffs_input.losvd193p1778-av0p4285-redshift0p0218.txt
#    I.e., the value of the parameters formatted with 4 
#    decimals and the '.' replaced to 'p'.
# 
#    Each coeff file should carry the ID, AGE, MET and the COEFF:
#
#    # ID MET AGE COEFF
#    0 3.7047000e-03 1.0000021e-03 5.7196858e-03
#    1 7.5640000e-03 1.0000021e-03 1.0281415e-02
#    2 1.8999999e-02 1.0000021e-03 5.3646386e-03
#    ...
#
####################################################
# For this particular example we use the SSP library
# gsd01_156.fits to generate the spectrum and the same
# library to fit it. The compact version of this 
# library (gsd01_12.fits) is used to the non-linear
# fit.
# We also leave a 2000 examples of coeffs files and
# a real_parameters.csv file containing all of them.
####################################################
import io
import sys
import glob
import shutil
import numpy as np
import pandas as pd
from os import makedirs
from copy import deepcopy as copy
from os.path import basename, join
from contextlib import redirect_stdout

from pyFIT3D.common.io import output_spectra 
from pyFIT3D.modelling.stellar import SSPModels
from pyFIT3D.common.auto_ssp_tools import auto_ssp_spec

dtype_coeffs_file = [
    ('id','int'), ('age', 'float'), ('met', 'float'), ('coeff', 'float'), ('min_coeff', 'float'),
    ('l_ML', 'float'), ('AV', 'float'), ('norm_coeff', 'float'), ('err_coeff', 'float'),
]

def loop_simul(pars_dataframe):
    if isinstance(pars_dataframe, str):
        pars_dataframe = pd.read_csv(pars_dataframe, dtype=np.float)
    losvd = (pars_dataframe['LOSVD']).map('{:.4f}'.format)
    Av = (pars_dataframe['Av']).map('{:.4f}'.format)
    redshift = (pars_dataframe['redshift']).map('{:.4f}'.format)
    u = {'LOSVD': 'km/s', 'Av': 'mag'}
    _zipped = zip(losvd.tolist(), Av.tolist(), redshift.tolist())
    for i_spec, (_losvd, _Av, _redshift) in enumerate(_zipped):
        str_losvd = 'losvd' + _losvd.replace('.', 'p')
        str_Av = 'av' + _Av.replace('.', 'p')
        str_redshift = 'redshift' + _redshift.replace('.', 'p')
        pars_tag = f'{str_losvd}-{str_Av}-{str_redshift}'
        yield i_spec, pars_tag

def read_pars_coeffs(pars_filename, input_coeffs_dir):
    def fix_coeffs_df(df):
        unique_ids = df.id.drop_duplicates().values
        _df = []
        for chunk in range(len(df) // unique_ids.size):
            ini = chunk*unique_ids.size
            _df.append(df.iloc[ini:ini + unique_ids.size, :].copy().reset_index(drop=True))
        return _df

    real_pars = pd.read_csv(pars_filename, dtype=np.float)
    names = [x[0] for x in dtype_coeffs_file]
    real_coeffs = None
    for i_spec, pars_tag in loop_simul(real_pars):
        rcoeffs_file = join(input_coeffs_dir, f'coeffs_input.{pars_tag}.txt')
        x = pd.read_csv(rcoeffs_file, sep='\s+', comment='#', names=names)
        real_coeffs = real_coeffs.append(x) if real_coeffs is not None else x
    real_coeffs = fix_coeffs_df(real_coeffs.reset_index(drop=True))
    return real_pars, real_coeffs

In [2]:
ssp_models_file = 'gsd01_156.fits'
config_file = 'auto_ssp.config'
nl_ssp_models_file = 'gsd01_12.fits'
mask_list = None  
wl_range = [3800, 7000]
nl_wl_range = [3800, 4700]
fit_gas = False
elines_mask_file = None
number_of_simulations = 1

pars_file = 'real_parameters.csv'

z_min_max = [0.001, 0.1]
sigma_min_max = [0, 350]
Av_min_max = [0, 1.6]
log_noise_min_max = [-4, -0.5]

input_coeffs_path = 'input_coeffs'

_, __ = read_pars_coeffs(pars_file, input_coeffs_path)
z__s, sigma__s, Av__s = _.redshift, _.LOSVD, _.Av
coeffs__n = [x.coeff for x in __]
nsim = len(coeffs__n)
if number_of_simulations > nsim:
    number_of_simulations = nsim

models = SSPModels(ssp_models_file)
n_coeffs = models.n_models
wl = models.wavelength
msk = wl % 2 == 0
wl = wl[msk]

output_path = 'output_analysis'
input_path = 'input_spec'

# Create input directory
try:
    makedirs(input_path)
except FileExistsError:
    print(f'{basename(sys.argv[0])}: {input_path}: directory already exists')

# Create output directory
try:
    makedirs(output_path)
except FileExistsError:
    print(f'{basename(sys.argv[0])}: {output_path}: directory already exists')

with open('simulation.out', 'w') as fsim:
    with redirect_stdout(fsim):
        for i, _otag in loop_simul(pars_file):
            if i >= number_of_simulations:
                continue

            l_noise = log_noise_min_max[0] + np.diff(log_noise_min_max)[0]*np.random.rand()
            noise = 10**l_noise

            ###############
            # CREATE SPEC
            ###############
            # This part where everything can be changed. This is only a simple example
            # on how to create a spectrum with the coefficients, kinematics and dust
            # extinction. Example: Coeffs can be generated with tau-models; randomly 
            # chosen, etc.
            coeffs = coeffs__n[i]
            z = z__s[i]
            sigma = sigma__s[i]
            Av = Av__s[i]
            print(f'inputs: z:{z} - sigma:{sigma} - AV:{Av}')
            flux = models.get_model_from_coeffs(
                coeffs=coeffs, wavelength=wl, redshift=z,
                sigma=sigma, AV=Av, sigma_inst=0.001
            )
            # generate bogus noise and eflux
            flux_range = flux.max() - flux.min()
            perturbed_flux__w = flux + np.random.normal(0, 0.1*flux_range*noise, flux.size)
            eflux__w = 0.001*perturbed_flux__w
            spec_name = join(output_path, f'spec_{_otag}.txt')
            # save spectrum
            output_spectra(wl, [perturbed_flux__w, eflux__w], spec_name)
            ##################
            # END CREATE SPEC
            ##################

            ###############
            # FIT SPEC
            ###############
            # This part uses pyFIT3D.common.auto_ssp_tools.auto_ssp_spec() to 
            # analyze the spectrum created above. This functions uses the input
            # data from files.
            auto_ssp_filename = f'auto_ssp_{_otag}.out'
            auto_ssp_spec(spec_file=spec_name, ssp_models_file=ssp_models_file,
                          out_file=auto_ssp_filename, config_file=config_file,
                          nl_ssp_models_file=nl_ssp_models_file,
                          instrumental_dispersion=0.001,
                          wl_range=wl_range, nl_wl_range=nl_wl_range,
                          mask_list=mask_list, elines_mask_file=elines_mask_file,
                          redshift_set=[0.01, 0.001, z_min_max[0]*0.95, z_min_max[1]*1.05],
                          losvd_set=[30, 10, sigma_min_max[0]*0.95, sigma_min_max[1]*1.05],
                          AV_set=[0.15, 0.05, Av_min_max[0]*0.95, Av_min_max[1]*1.05],
                          R_V=3.1, extlaw='CCM', fit_gas=fit_gas, fit_sigma_rnd=True,
                          plot=0, verbose=0)
            ###############
            # END FIT SPEC
            ###############

            # Move output analysis
            for file in glob.glob(f'*{auto_ssp_filename}*'):
                shutil.move(src=file, dst=join(output_path, file))